Epocs = 100, dataset 4000 

In [1]:
import pandas as pd
import glob
import numpy
import csv
from nltk.tokenize import word_tokenize
import xlrd
import re
from nltk import bigrams
from nltk import ngrams
import operator
from collections import Counter
from nltk.corpus import stopwords
import string
import matplotlib.pyplot as plt

In [2]:
from random import randint
from numpy import array
from numpy import argmax
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [3]:
path = r'E:\Level 4 Project\dataset\final\preprocess' # use your path
all_files = glob.glob(path + "/*.csv")

In [4]:
li = []

In [5]:
for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

In [6]:
df = pd.concat(li, axis=0, ignore_index=True, sort=False)

In [7]:
df.head()

Date  \
0  2014-01-01 23:59:47+00:00    
1  2014-01-01 23:57:47+00:00    
2  2014-01-01 23:56:21+00:00    
3  2014-01-01 23:56:03+00:00    
4  2014-01-01 23:55:55+00:00    

                                               Tweet  
0   Clearwater Beach,FL Scattered Thunderstorms t...  
1   Tourism disappeared because of Troubles: To...  
2   I'm at Department of Tourism and Hospitality ...  
3   'Like a Napa Valley wine tour': Pot tourism r...  
4           Focus : Recreation & Tourism Planning .

In [8]:
df.shape

(5492006, 2)

In [9]:
emoticons_str = r"""
    (?:
        [:=;] # Eyes
        [oO\-]? # Nose (optional)
        [D\)\]\(\]/\\OpP] # Mouth
    )"""

In [10]:
def preprocess_fornothash(s, lowercase=True):
    tokens = tokenize_fornothash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_fornothash(s):
    return tokens_re_fornothash.findall(s)


regex_str_fornothash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    #r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_fornothash = re.compile(r'(' + '|'.join(regex_str_fornothash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [11]:
def preprocess_forhash(s, lowercase=True):
    tokens = tokenize_forhash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_forhash(s):
    return tokens_re_forhash.findall(s)

regex_str_forhash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_forhash = re.compile(r'(' + '|'.join(regex_str_forhash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [12]:
punctuation = list(string.punctuation)
unnecssary = ['The','tourism','I','rt', 'via','...','â','click']
unnecssary_hash = ['#','#tourism']
ascii_words = ['\x92','\x96']
years = ['2018','2017','2016','2015','2014','2013']
numbers = ['nine']
stop = stopwords.words('english') + punctuation + unnecssary + ascii_words + years + unnecssary_hash + numbers

count_all = []
popular_common_words = []
i=0
sets=4000

c =0
for x in range(sets):
    count_all.append(Counter())

for y in range(sets):
    for x in range(1, 500):
        value = df.loc[i, "Tweet"]

        #terms_all = [term for term in preprocess_fornothash(value) if term not in stop]  
        terms_all = [term for term in preprocess_forhash(value)
                  if term.startswith('#') if term not in stop]
        i = i + 1
        count_all[y].update(terms_all)
    
    popular_common_words.append(count_all[y].most_common(5))
        

In [13]:
trendingTopicsAll = []

def processTrendingArray(str):
    global trendingTopicsAll
    b = [i for i,x in enumerate(trendingTopicsAll) if x == str]
    if(b == []):
        trendingTopicsAll.append(str)
        return len(trendingTopicsAll)-1
    else:
        return b[0]

In [14]:
trendingTopicsInEachDays = []
trendingIdsInEachDays = []
for index, y in enumerate(popular_common_words):
    trendingTopicsInEachDays.append([])
    trendingIdsInEachDays.append([])
    for x in y:
        trendingTopicsInEachDays[index].append(x[0])
        trendingIdsInEachDays[index].append(processTrendingArray(x[0]))
        

# print(trendingTopicsInEachDays)
# print("####################")
print(trendingTopicsAll)
# print("####################")
# print(trendingIdsInEachDays)

['#travel', '#news', '#amsterdam', '#netherlands', '#holland', '#smtravel', '#trip', '#photo', '#marijuana', '#travelers', '#latestnews', '#street', '#htmi', '#colorado', '#pakistan', '#adventure', '#maldives', '#town', '#road', '#jobs', '#aglasem', '#infografia', '#infographic', '#googlenews', '#webdesign', '#vatican', '#popefrancis', '#business', '#amazing', '#chile', '#ttot', '#hhi', '#cnn', '#culture', '#carrefour', '#muscat', '#egypt', '#blog', '#saveswedenswolves', '#backpacking', '#welcome_to_egypt', '#alanailham', '#thailand', '#vmy2014', '#haiti', '#photography', '#church', '#southafrica', '#qatar', '#malaysia', '#hospitality', '#hotels', '#food', '#neworleanswill', '#cruisepeople', '#ofc14', '#china', '#rwanda', '#ecuador', '#keepwolveslisted', '#nysos14', '#expediachat', '#africa', '#job', '#tech', '#socialmedia', '#mashable', '#gdaytourism', '#ireland', '#hampi', '#uganda', '#scotlandhour', '#twitter', '#marketing', '#talent4hire', '#sayfie', '#ff', '#oman', '#caribbean', '

In [ ]:
# generate a sequence of random numbers in [0, 99]
tweetIdsCount = -1
inputs = len(trendingTopicsAll)

def generate_sequence():
    global tweetIdsCount
    print("tweetIdsCount - ",tweetIdsCount)
    tweetIdsCount = tweetIdsCount+1
    return (trendingIdsInEachDays[tweetIdsCount])
    #return [23,12,45]
    
# one hot encode sequence
def one_hot_encode(sequence, n_unique=inputs):
	encoding = list()
	for value in sequence:
		vector = [0 for _ in range(n_unique)]
		vector[value] = 1
		encoding.append(vector)
	return array(encoding)
 
# decode a one hot encoded string
def one_hot_decode(encoded_seq):
	return [argmax(vector) for vector in encoded_seq]
 
# generate data for the lstm
def generate_data():
	# generate sequence
	sequence = generate_sequence()
	# one hot encode
	encoded = one_hot_encode(sequence)
	# convert to 3d for input
	X = encoded.reshape(encoded.shape[0], 1, encoded.shape[1])
	return X, encoded    
    
# define model
model = Sequential() 
model.add(LSTM(50, input_shape=(1, inputs)))
model.add(Dense(inputs, activation='relu'))
model.add(Dense(inputs, activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit model
for i in range(3000):
	X, y = generate_data()
	model.fit(X, y, epochs=100, batch_size=1, verbose=2)
# evaluate model on new data
X, y = generate_data()
yhat = model.predict(X)

#print('Expected:  %s' % one_hot_decode(y))
#print('Predicted: %s' % one_hot_decode(yhat))

a = []
b = []
i = 0;
# for x in range(5):
#     if(one_hot_decode(y)[x] == one_hot_decode(yhat)[x]):
#         i += 1
#     a.append(trendingTopicsAll[one_hot_decode(y)[x]])
#     b.append(trendingTopicsAll[one_hot_decode(yhat)[x]])
   
# print("Expected: ",a)
# print("Predicted: ",b)
# print("Test Accuracy: ",(i/5)*100)

W0118 03:06:19.998383  8996 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:1251: calling VarianceScaling.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


tweetIdsCount -  -1


W0118 03:06:21.022375  8996 deprecation.py:323] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\math_grad.py:1250: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


Epoch 1/100
5/5 - 3s - loss: 7.8560 - acc: 0.0000e+00
Epoch 2/100
5/5 - 0s - loss: 7.8021 - acc: 0.4000
Epoch 3/100
5/5 - 0s - loss: 7.7302 - acc: 0.2000
Epoch 4/100
5/5 - 0s - loss: 7.6114 - acc: 0.4000
Epoch 5/100
5/5 - 0s - loss: 7.4193 - acc: 0.2000
Epoch 6/100
5/5 - 0s - loss: 7.1232 - acc: 0.2000
Epoch 7/100
5/5 - 0s - loss: 6.6626 - acc: 0.2000
Epoch 8/100
5/5 - 0s - loss: 5.9565 - acc: 0.2000
Epoch 9/100
5/5 - 0s - loss: 4.9638 - acc: 0.2000
Epoch 10/100
5/5 - 0s - loss: 3.5964 - acc: 0.2000
Epoch 11/100
5/5 - 0s - loss: 2.2514 - acc: 0.2000
Epoch 12/100
5/5 - 0s - loss: 1.6746 - acc: 0.2000
Epoch 13/100
5/5 - 0s - loss: 1.5760 - acc: 0.2000
Epoch 14/100
5/5 - 0s - loss: 1.5377 - acc: 0.4000
Epoch 15/100
5/5 - 0s - loss: 1.5210 - acc: 0.4000
Epoch 16/100
5/5 - 0s - loss: 1.4926 - acc: 0.8000
Epoch 17/100
5/5 - 0s - loss: 1.4715 - acc: 0.4000
Epoch 18/100
5/5 - 0s - loss: 1.4636 - acc: 0.8000
Epoch 19/100
5/5 - 0s - loss: 1.4210 - acc: 1.0000
Epoch 20/100
5/5 - 0s - loss: 1.3955

Epoch 62/100
5/5 - 0s - loss: 0.0063 - acc: 1.0000
Epoch 63/100
5/5 - 0s - loss: 0.0059 - acc: 1.0000
Epoch 64/100
5/5 - 0s - loss: 0.0056 - acc: 1.0000
Epoch 65/100
5/5 - 0s - loss: 0.0053 - acc: 1.0000
Epoch 66/100
5/5 - 0s - loss: 0.0050 - acc: 1.0000
Epoch 67/100
5/5 - 0s - loss: 0.0047 - acc: 1.0000
Epoch 68/100
5/5 - 0s - loss: 0.0044 - acc: 1.0000
Epoch 69/100
5/5 - 0s - loss: 0.0042 - acc: 1.0000
Epoch 70/100
5/5 - 0s - loss: 0.0040 - acc: 1.0000
Epoch 71/100
5/5 - 0s - loss: 0.0038 - acc: 1.0000
Epoch 72/100
5/5 - 0s - loss: 0.0036 - acc: 1.0000
Epoch 73/100
5/5 - 0s - loss: 0.0035 - acc: 1.0000
Epoch 74/100
5/5 - 0s - loss: 0.0033 - acc: 1.0000
Epoch 75/100
5/5 - 0s - loss: 0.0031 - acc: 1.0000
Epoch 76/100
5/5 - 0s - loss: 0.0030 - acc: 1.0000
Epoch 77/100
5/5 - 0s - loss: 0.0028 - acc: 1.0000
Epoch 78/100
5/5 - 0s - loss: 0.0027 - acc: 1.0000
Epoch 79/100
5/5 - 0s - loss: 0.0026 - acc: 1.0000
Epoch 80/100
5/5 - 0s - loss: 0.0025 - acc: 1.0000
Epoch 81/100
5/5 - 0s - loss: 0

...

Epoch 75/100
5/5 - 0s - loss: 1.6999e-05 - acc: 1.0000
Epoch 76/100
5/5 - 0s - loss: 1.6474e-05 - acc: 1.0000
Epoch 77/100
5/5 - 0s - loss: 1.6141e-05 - acc: 1.0000
Epoch 78/100
5/5 - 0s - loss: 1.5783e-05 - acc: 1.0000
Epoch 79/100
5/5 - 1s - loss: 1.5378e-05 - acc: 1.0000
Epoch 80/100
5/5 - 0s - loss: 1.4996e-05 - acc: 1.0000
Epoch 81/100
5/5 - 1s - loss: 1.4615e-05 - acc: 1.0000
Epoch 82/100
5/5 - 0s - loss: 1.4281e-05 - acc: 1.0000
Epoch 83/100
5/5 - 0s - loss: 1.3923e-05 - acc: 1.0000
Epoch 84/100
5/5 - 0s - loss: 1.3661e-05 - acc: 1.0000
Epoch 85/100
5/5 - 0s - loss: 1.3280e-05 - acc: 1.0000
Epoch 86/100
5/5 - 0s - loss: 1.3041e-05 - acc: 1.0000
Epoch 87/100
5/5 - 1s - loss: 1.2827e-05 - acc: 1.0000
Epoch 88/100
5/5 - 0s - loss: 1.2517e-05 - acc: 1.0000
Epoch 89/100
5/5 - 0s - loss: 1.2350e-05 - acc: 1.0000
Epoch 90/100
5/5 - 0s - loss: 1.1992e-05 - acc: 1.0000
Epoch 91/100
5/5 - 0s - loss: 1.1802e-05 - acc: 1.0000
Epoch 92/100
5/5 - 0s - loss: 1.1611e-05 - acc: 1.0000
Epoch 93/1

Epoch 25/100
5/5 - 0s - loss: 2.0375e-04 - acc: 1.0000
Epoch 26/100
5/5 - 1s - loss: 1.9319e-04 - acc: 1.0000
Epoch 27/100
5/5 - 0s - loss: 1.8823e-04 - acc: 1.0000
Epoch 28/100
5/5 - 1s - loss: 1.7698e-04 - acc: 1.0000
Epoch 29/100
5/5 - 0s - loss: 1.7074e-04 - acc: 1.0000
Epoch 30/100
5/5 - 1s - loss: 1.6521e-04 - acc: 1.0000
Epoch 31/100
5/5 - 0s - loss: 1.5835e-04 - acc: 1.0000
Epoch 32/100
5/5 - 1s - loss: 1.5399e-04 - acc: 1.0000
Epoch 33/100
5/5 - 0s - loss: 1.4622e-04 - acc: 1.0000
Epoch 34/100
5/5 - 0s - loss: 1.4166e-04 - acc: 1.0000
Epoch 35/100
5/5 - 0s - loss: 1.3809e-04 - acc: 1.0000
Epoch 36/100
5/5 - 0s - loss: 1.3356e-04 - acc: 1.0000
Epoch 37/100
5/5 - 0s - loss: 1.2970e-04 - acc: 1.0000
Epoch 38/100
5/5 - 1s - loss: 1.2553e-04 - acc: 1.0000
Epoch 39/100
5/5 - 0s - loss: 1.2112e-04 - acc: 1.0000
Epoch 40/100
5/5 - 1s - loss: 1.1645e-04 - acc: 1.0000
Epoch 41/100
5/5 - 0s - loss: 1.1292e-04 - acc: 1.0000
Epoch 42/100
5/5 - 1s - loss: 1.1125e-04 - acc: 1.0000
Epoch 43/1

Epoch 75/100
5/5 - 0s - loss: 3.6975e-05 - acc: 1.0000
Epoch 76/100
5/5 - 0s - loss: 3.5903e-05 - acc: 1.0000
Epoch 77/100
5/5 - 0s - loss: 3.5378e-05 - acc: 1.0000
Epoch 78/100
5/5 - 0s - loss: 3.4091e-05 - acc: 1.0000
Epoch 79/100
5/5 - 0s - loss: 3.2327e-05 - acc: 1.0000
Epoch 80/100
5/5 - 0s - loss: 3.1922e-05 - acc: 1.0000
Epoch 81/100
5/5 - 0s - loss: 3.1016e-05 - acc: 1.0000
Epoch 82/100
5/5 - 0s - loss: 2.9514e-05 - acc: 1.0000
Epoch 83/100
5/5 - 0s - loss: 2.8847e-05 - acc: 1.0000
Epoch 84/100
5/5 - 1s - loss: 2.7965e-05 - acc: 1.0000
Epoch 85/100
5/5 - 0s - loss: 2.7011e-05 - acc: 1.0000
Epoch 86/100
5/5 - 1s - loss: 2.6653e-05 - acc: 1.0000
Epoch 87/100
5/5 - 0s - loss: 2.5581e-05 - acc: 1.0000
Epoch 88/100
5/5 - 1s - loss: 2.4794e-05 - acc: 1.0000
Epoch 89/100
5/5 - 0s - loss: 2.4079e-05 - acc: 1.0000
Epoch 90/100
5/5 - 1s - loss: 2.3078e-05 - acc: 1.0000
Epoch 91/100
5/5 - 0s - loss: 2.2505e-05 - acc: 1.0000
Epoch 92/100
5/5 - 1s - loss: 2.2029e-05 - acc: 1.0000
Epoch 93/1

Epoch 24/100
5/5 - 1s - loss: 0.0000e+00 - acc: 1.0000
Epoch 25/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 26/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 27/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 28/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 29/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 30/100
5/5 - 1s - loss: 0.0000e+00 - acc: 1.0000
Epoch 31/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 32/100
5/5 - 1s - loss: 0.0000e+00 - acc: 1.0000
Epoch 33/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 34/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 35/100
5/5 - 1s - loss: 0.0000e+00 - acc: 1.0000
Epoch 36/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 37/100
5/5 - 1s - loss: 0.0000e+00 - acc: 1.0000
Epoch 38/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 39/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 40/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 41/100
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 42/1

Epoch 74/100
5/5 - 0s - loss: 1.3756e-05 - acc: 1.0000
Epoch 75/100
5/5 - 0s - loss: 1.3566e-05 - acc: 1.0000
Epoch 76/100
5/5 - 0s - loss: 1.3303e-05 - acc: 1.0000
Epoch 77/100
5/5 - 0s - loss: 1.3017e-05 - acc: 1.0000
Epoch 78/100
5/5 - 0s - loss: 1.2898e-05 - acc: 1.0000
Epoch 79/100
5/5 - 0s - loss: 1.2588e-05 - acc: 1.0000
Epoch 80/100
5/5 - 0s - loss: 1.2421e-05 - acc: 1.0000
Epoch 81/100
5/5 - 0s - loss: 1.2016e-05 - acc: 1.0000
Epoch 82/100
5/5 - 0s - loss: 1.1897e-05 - acc: 1.0000
Epoch 83/100
5/5 - 0s - loss: 1.1706e-05 - acc: 1.0000
Epoch 84/100
5/5 - 0s - loss: 1.1396e-05 - acc: 1.0000
Epoch 85/100
5/5 - 0s - loss: 1.1205e-05 - acc: 1.0000
Epoch 86/100
5/5 - 0s - loss: 1.1015e-05 - acc: 1.0000
Epoch 87/100
5/5 - 0s - loss: 1.0919e-05 - acc: 1.0000
Epoch 88/100
5/5 - 0s - loss: 1.0657e-05 - acc: 1.0000
Epoch 89/100
5/5 - 0s - loss: 1.0395e-05 - acc: 1.0000
Epoch 90/100
5/5 - 0s - loss: 1.0252e-05 - acc: 1.0000
Epoch 91/100
5/5 - 0s - loss: 1.0013e-05 - acc: 1.0000
Epoch 92/1

In [ ]:
print(tweetIdsCount)
testaccuracy = []

def getOneAccuracy(a,b):
    i = 0;
    for x in range(5):
        if(a[x] == b[x]):
            i += 1
    return i/5

def getTestData():
    for i in range(990):
        X, y = generate_data()
        yhat = model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))
    
getTestData()
print(testaccuracy)
print('average - ',sum(testaccuracy) / len(testaccuracy))

In [ ]:
len(trendingTopicsAll)

In [19]:
from tensorflow.keras.models import model_from_json

In [20]:
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model.h5")
print("Saved model to disk")

Saved model to disk


In [21]:
json_file = open('model.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights("model.h5")
print("Loaded model from disk")

W0117 23:59:24.137207 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling GlorotUniform.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
W0117 23:59:24.143220 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling Orthogonal.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
W0117 23:59:24.147231 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling Zeros.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and

Loaded model from disk


In [22]:
loaded_model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [23]:
X, y = generate_data()
yhat = loaded_model.predict(X)
print('Expected:  %s' % one_hot_decode(y))
print('Predicted: %s' % one_hot_decode(yhat))

tweetIdsCount -  2990
Expected:  [0, 730, 73, 118, 81]
Predicted: [0, 730, 73, 118, 81]


In [24]:
def getTestData():
    for i in range(9):
        X, y = generate_data()
        yhat = loaded_model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))

In [25]:
getTestData()
print(testaccuracy)

tweetIdsCount -  2991
Expected:  [0, 1929, 730, 73, 1930]
Predicted: [0, 1420, 730, 73, 1420]
tweetIdsCount -  2992
Expected:  [0, 1931, 730, 73, 602]
Predicted: [0, 1420, 730, 73, 602]
tweetIdsCount -  2993
Expected:  [0, 730, 73, 1932, 1933]
Predicted: [0, 730, 73, 1420, 1420]
tweetIdsCount -  2994
Expected:  [0, 730, 36, 537, 95]
Predicted: [0, 730, 36, 1399, 95]
tweetIdsCount -  2995
Expected:  [0, 73, 730, 1447, 794]
Predicted: [0, 73, 730, 1420, 794]
tweetIdsCount -  2996
Expected:  [0, 1402, 730, 73, 1]
Predicted: [0, 1402, 730, 73, 1]
tweetIdsCount -  2997
Expected:  [0, 118, 494, 730, 73]
Predicted: [0, 118, 494, 730, 73]
tweetIdsCount -  2998
Expected:  [0, 73, 730, 134, 833]
Predicted: [0, 73, 730, 134, 833]
tweetIdsCount -  2999


IndexError: list index out of range